In [ ]:

import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from scipy.sparse import diags, identity, kron
from scipy.sparse.linalg import splu

# Parámetros físicos - numéricos
L = 1
Nx = 320
Ny = 320
dx = L / (Nx + 1)
dy = L / (Ny + 1)
x = np.linspace(0, L, Nx + 2)
y = np.linspace(0, L, Ny + 2)
X, Y = np.meshgrid(x, y)

T = 0.8
dt = 1e-4
Nt = int(T / dt)

hbar = 1.0
m = 1.0
s = 1j * hbar * dt / (4 * m * dx**2)

# Condición inicial: paquete gaussiano localizado 2D 
x0, y0 = .5, .5
sigma = 0.08
k0 = 0.0
theta = 0 * np.pi/2*0
#np.pi / 12 * 0   # dirección del momentum partícula (radianes)

k0x = k0 * np.cos(theta)
k0y = k0 * np.sin(theta)
fase = np.exp(1j * (k0x * X + k0y * Y))

psi0_2D = np.exp(-((X - x0)**2 + (Y - y0)**2) / (2 * sigma**2)) * fase
psi0_2D[0, :] = psi0_2D[-1, :] = 0.0
psi0_2D[:, 0] = psi0_2D[:, -1] = 0.0

# Reorganizar psi en vector columna
psi = psi0_2D[1:-1, 1:-1].flatten()

# Laplaciano 2D con producto de Kronecker
Ix = identity(Nx)
Iy = identity(Ny)
Dx = diags([-1, 2, -1], [-1, 0, 1], shape=(Nx, Nx))
Dy = diags([-1, 2, -1], [-1, 0, 1], shape=(Ny, Ny))
Laplacian = kron(Iy, Dx) + kron(Dy, Ix)

# Matrices A y B para Crank-Nicholson
A = identity(Nx * Ny) + s * Laplacian
B = identity(Nx * Ny) - s * Laplacian
# Declaración LU para A fija 
LU = splu(A.tocsc()) 


# Evolución temporal, Iteraciones, resolución Sist. por LU
data = []
for n in range(Nt):
    b = B.dot(psi)
    psi = LU.solve(b)
    if n % 10 == 0:
        psi_grid = np.zeros((Ny + 2, Nx + 2), dtype=complex)
        psi_grid[1:-1, 1:-1] = psi.reshape((Ny, Nx))
        data.append(np.abs(psi_grid)**2)

# Animación
plt.style.use('dark_background')
fig, ax = plt.subplots()

im = ax.imshow(data[0], extent=[0, L, 0, L], origin='lower', cmap='inferno', vmin=0, vmax=np.max(data[0]))

ax.set_xlabel('x')
ax.set_ylabel('y')
ax.set_title('|ψ(x, y, t)|² evolution')

# Marca de autor
ax.text(0.5, 1.07, 'Simulation by Alexis F. Espinoza Q.', transform=ax.transAxes, fontsize=10, ha='center', va='bottom', color='white', alpha=0.7)

# Agregar barra de color para mostrar escala de valores de la desnidad de probabilidad
cbar = fig.colorbar(im, ax=ax)
cbar.set_label('Probability density |ψ|²')


def update(frame):
    im.set_data(data[frame])
    ax.set_title(f't = {frame * dt * 10:.5f} s')
    return [im]

ani = animation.FuncAnimation(fig, update, frames=len(data), blit=True)

# Guardar video
ani.save("cd190725.mp4", writer='ffmpeg', fps=30, dpi=300)
plt.close()

# Mostrar en notebook 
from IPython.display import HTML
HTML(ani.to_jshtml())